In [1]:
import pandas as pd
ch1 = pd.read_csv('./channel_1.dat', names=['Unix', 'Watt'],header=None, delimiter=" ")
print('Done!')

Done!


In [2]:
ch1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21837636 entries, 0 to 21837635
Data columns (total 2 columns):
 #   Column  Dtype
---  ------  -----
 0   Unix    int64
 1   Watt    int64
dtypes: int64(2)
memory usage: 333.2 MB


In [3]:
print(ch1[0:11])
print('1번째')
print(ch1[0:1])
print()
print('21837636번째')
print(ch1[21837635:21837636])

          Unix  Watt
0   1352500095   599
1   1352500101   582
2   1352500107   600
3   1352500113   586
4   1352500120   596
5   1352500132   581
6   1352500138   597
7   1352500144   592
8   1352500150   587
9   1352500156   574
10  1352500168   577
1번째
         Unix  Watt
0  1352500095   599

21837636번째
                Unix  Watt
21837635  1493227960   672


In [4]:
from datetime import datetime
ch1_date = pd.DataFrame(ch1,columns = ['Unix', 'Date', 'Watt'])

ch1_date['Date'] = pd.to_datetime(ch1['Unix'], unit='s')
ch1_date.info()
ch1_date.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21837636 entries, 0 to 21837635
Data columns (total 3 columns):
 #   Column  Dtype         
---  ------  -----         
 0   Unix    int64         
 1   Date    datetime64[ns]
 2   Watt    int64         
dtypes: datetime64[ns](1), int64(2)
memory usage: 499.8 MB


Unix                Date  Watt
0  1352500095 2012-11-09 22:28:15   599
1  1352500101 2012-11-09 22:28:21   582
2  1352500107 2012-11-09 22:28:27   600
3  1352500113 2012-11-09 22:28:33   586
4  1352500120 2012-11-09 22:28:40   596
5  1352500132 2012-11-09 22:28:52   581
6  1352500138 2012-11-09 22:28:58   597
7  1352500144 2012-11-09 22:29:04   592
8  1352500150 2012-11-09 22:29:10   587
9  1352500156 2012-11-09 22:29:16   574

### 정상 구동 버전 반복을 위한 코드

In [38]:
import time
import csv

# 1.
#i = 431368, 517000, 684157
i = 431368
print('Running!', '\n'*9)

# 2.
while(i < 20284836):
    list1 = ch1_date.loc[i].values.tolist()
            
    # Nested List 사용해서 시간 정보만 따로 추출
    date = list1[1]
    y1 = date.year
    M1 = date.month
    d1 = date.day
    H1 = date.hour # 이 H가 있어야 밑에 있는 하루 단위 반복이 돌 변수가 됨.
    n = 0
    
    # H1는 데이터에서 읽어오는 값이지만 H0는 절대적, 순차값
    
    # 3. 
    # 하루 단위 반복
    while(H1 < 24):
        H0 = 0
        
        watt_list=[]
        h = date.hour

        
        # h시와 h+1 시 사이 반복
        while(h < h+1):
            n=n+1
            list2 = ch1_date.loc[i].values.tolist()
            
            date = list2[1]
            watt = list2[2]
            
            y = date.year
            M = date.month
            d = date.day
            h = date.hour
            m = date.minute
            s = date.second
            
            print()
            
            # jump 를 하는 경우가 있기 때문에 이 경우를 구분 짓는 변수를 j로 선택
            j=h-H1
            
            
            # '시'단위가 바뀌기 전에 값들만 저장 (ex. 1시일 경우 2시가 되기전 데이터들만 저장)
            if(j==0):
                watt_list.append(watt) # 1시간 동안 6 or 7초 단위로 읽어오는 watt 값들 전부 추가
                
                # 확인용 각 변수 출력
                total_date = '{0}년 {1}월 {2}일 - {3}시 {4}분 {5}초'.format(y, M, d, h, m, s)
                print(total_date)
                print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'H0 >>', H0)
                print('칼럼 출력 >>', list2)
            
                i = i+1

                
            # 시가 바뀌는 경우 -------------------------------------------------------------------------------------------------
            elif (j==1):
                print('시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                #print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'H0 >>', H0)
                print('1시간 동안 데이터 수 >>', n)
                print()
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
    
                break
            
        
            # 1 시간치 정리가 끝나고 다음 날로 넘어가는 경우. 따로 설정함.---------------------------------------------------------
            elif(d1+1==d):
                print('========================================< 1시간치 끝!! >==================================================')
                #print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'H0 >>', H0)
                print('1시간 동안 데이터 수 >>', n)
                print()
                d=d-1
                h=h+24
        
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        

                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)
    
                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
                print('========================================< 하루 끝!! >==================================================')
                print('\n'*4)
                break
                

            # 1시간 단위 반복 중 에러 발생 경우-------------------------------------------------------------------------------------
            elif (n>600):
                print('wn'*9)
                print('데이터 처리 필요!! 반복 루프 강제 종료')
                print('X'*500)
                print('wn'*9)
                break

                
    
            # 시 단위가 순차적으로 넘어가는 것이 아닌 건너뛰고 점프해버린 경우 ---------------------------------------------------
            else:
                # 일단 해당 시각 존재하는 만큼은 정리해서 맥스값을 추출하고~
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')
                print()
                
                print('========================================< 1시간치 끝!! >==================================================')
                print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'H0 >>', H0)
                print('1시간 동안 데이터 수 >>', n)
                print()
                
                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)
        
                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')
                
                jc=j
                # 건너뛴 횟수만큼 빈 시간대를 Null로 저장
                while(True):
                    h=h+1
                    # 점프한 시각 이전까지 Null로 입력 
                    hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-j)
                    hourly_list = []
                    hourly_list.append(hourly_date)
                    hourly_list.append('Null')

                    # 데이터 저장 
                    with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                        writer = csv.writer(file)
                        writer.writerow(hourly_list)       
                    print('csv 저장 완료!')
                    
                    jc=jc-1
                    
                    if jc==1:
                        break
        
                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                #H0 = H0+1
                print('\n'*4)
    
                break
        
        print('여기를 거칩니다잇')
        break
        
        
    
    # 하루단위 while 여기서 브레이크를 걸고 다음날로 넘어가도록 해야함.
    
# 전체 While문 종료 지점

Running! 










2013년 1월 1일 - 0시 0분 1초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431368 H0 >> 0
칼럼 출력 >> [1356998401, Timestamp('2013-01-01 00:00:01'), 499]

2013년 1월 1일 - 0시 0분 7초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431369 H0 >> 0
칼럼 출력 >> [1356998407, Timestamp('2013-01-01 00:00:07'), 500]

2013년 1월 1일 - 0시 0분 13초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431370 H0 >> 0
칼럼 출력 >> [1356998413, Timestamp('2013-01-01 00:00:13'), 515]

2013년 1월 1일 - 0시 0분 19초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431371 H0 >> 0
칼럼 출력 >> [1356998419, Timestamp('2013-01-01 00:00:19'), 522]

2013년 1월 1일 - 0시 0분 26초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431372 H0 >> 0
칼럼 출력 >> [1356998426, Timestamp('2013-01-01 00:00:26'), 508]

2013년 1월 1일 - 0시 0분 32초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431373 H0 >> 0
칼럼 출력 >> [1356998432, Timestamp('2013-01-01 00:00:32'), 502]

2013년 1월 1일 - 0시 0분 38초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431374 H0 >> 0
칼럼 출력 >> [1356998438, Timestamp('2013-01-01

칼럼 출력 >> [1356999618, Timestamp('2013-01-01 00:20:18'), 434]

2013년 1월 1일 - 0시 20분 24초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431548 H0 >> 0
칼럼 출력 >> [1356999624, Timestamp('2013-01-01 00:20:24'), 434]

2013년 1월 1일 - 0시 20분 30초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431549 H0 >> 0
칼럼 출력 >> [1356999630, Timestamp('2013-01-01 00:20:30'), 449]

2013년 1월 1일 - 0시 20분 37초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431550 H0 >> 0
칼럼 출력 >> [1356999637, Timestamp('2013-01-01 00:20:37'), 449]

2013년 1월 1일 - 0시 20분 43초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431551 H0 >> 0
칼럼 출력 >> [1356999643, Timestamp('2013-01-01 00:20:43'), 449]

2013년 1월 1일 - 0시 20분 49초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431552 H0 >> 0
칼럼 출력 >> [1356999649, Timestamp('2013-01-01 00:20:49'), 449]

2013년 1월 1일 - 0시 20분 55초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431553 H0 >> 0
칼럼 출력 >> [1356999655, Timestamp('2013-01-01 00:20:55'), 443]

2013년 1월 1일 - 0시 21분 1초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431554 H


2013년 1월 1일 - 0시 42분 37초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431760 H0 >> 0
칼럼 출력 >> [1357000957, Timestamp('2013-01-01 00:42:37'), 521]

2013년 1월 1일 - 0시 42분 44초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431761 H0 >> 0
칼럼 출력 >> [1357000964, Timestamp('2013-01-01 00:42:44'), 513]

2013년 1월 1일 - 0시 42분 50초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431762 H0 >> 0
칼럼 출력 >> [1357000970, Timestamp('2013-01-01 00:42:50'), 509]

2013년 1월 1일 - 0시 42분 56초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431763 H0 >> 0
칼럼 출력 >> [1357000976, Timestamp('2013-01-01 00:42:56'), 517]

2013년 1월 1일 - 0시 43분 2초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431764 H0 >> 0
칼럼 출력 >> [1357000982, Timestamp('2013-01-01 00:43:02'), 506]

2013년 1월 1일 - 0시 43분 8초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431765 H0 >> 0
칼럼 출력 >> [1357000988, Timestamp('2013-01-01 00:43:08'), 516]

2013년 1월 1일 - 0시 43분 14초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431766 H0 >> 0
칼럼 출력 >> [1357000994, Timestamp('2013-01-01 00:43:14'),

csv 저장 완료!





여기를 거칩니다잇

2013년 1월 1일 - 1시 0분 5초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 431925 H0 >> 0
칼럼 출력 >> [1357002005, Timestamp('2013-01-01 01:00:05'), 2475]

2013년 1월 1일 - 1시 0분 11초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 431926 H0 >> 0
칼럼 출력 >> [1357002011, Timestamp('2013-01-01 01:00:11'), 2481]

2013년 1월 1일 - 1시 0분 17초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 431927 H0 >> 0
칼럼 출력 >> [1357002017, Timestamp('2013-01-01 01:00:17'), 2477]

2013년 1월 1일 - 1시 0분 22초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 431928 H0 >> 0
칼럼 출력 >> [1357002022, Timestamp('2013-01-01 01:00:22'), 2476]

2013년 1월 1일 - 1시 0분 28초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 431929 H0 >> 0
칼럼 출력 >> [1357002028, Timestamp('2013-01-01 01:00:28'), 2477]

2013년 1월 1일 - 1시 0분 34초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 431930 H0 >> 0
칼럼 출력 >> [1357002034, Timestamp('2013-01-01 01:00:34'), 2473]

2013년 1월 1일 - 1시 0분 40초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 431931 H0 >> 0
칼럼 출력 >> [1357002040, Timesta

칼럼 출력 >> [1357003237, Timestamp('2013-01-01 01:20:37'), 282]

2013년 1월 1일 - 1시 20분 43초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 432123 H0 >> 0
칼럼 출력 >> [1357003243, Timestamp('2013-01-01 01:20:43'), 280]

2013년 1월 1일 - 1시 20분 49초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 432124 H0 >> 0
칼럼 출력 >> [1357003249, Timestamp('2013-01-01 01:20:49'), 280]

2013년 1월 1일 - 1시 20분 55초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 432125 H0 >> 0
칼럼 출력 >> [1357003255, Timestamp('2013-01-01 01:20:55'), 284]

2013년 1월 1일 - 1시 21분 2초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 432126 H0 >> 0
칼럼 출력 >> [1357003262, Timestamp('2013-01-01 01:21:02'), 280]

2013년 1월 1일 - 1시 21분 8초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 432127 H0 >> 0
칼럼 출력 >> [1357003268, Timestamp('2013-01-01 01:21:08'), 283]

2013년 1월 1일 - 1시 21분 14초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 432128 H0 >> 0
칼럼 출력 >> [1357003274, Timestamp('2013-01-01 01:21:14'), 280]

2013년 1월 1일 - 1시 21분 20초
d1 >> 1 d >> 1 H1 >> 1 h >> 1   //   i >> 432129 H0

...

d1 >> 1 d >> 1 H1 >> 2 h >> 2   //   i >> 432879 H0 >> 0
칼럼 출력 >> [1357008081, Timestamp('2013-01-01 02:41:21'), 183]

2013년 1월 1일 - 2시 41분 27초
d1 >> 1 d >> 1 H1 >> 2 h >> 2   //   i >> 432880 H0 >> 0
칼럼 출력 >> [1357008087, Timestamp('2013-01-01 02:41:27'), 182]

2013년 1월 1일 - 2시 41분 33초
d1 >> 1 d >> 1 H1 >> 2 h >> 2   //   i >> 432881 H0 >> 0
칼럼 출력 >> [1357008093, Timestamp('2013-01-01 02:41:33'), 178]

2013년 1월 1일 - 2시 41분 39초
d1 >> 1 d >> 1 H1 >> 2 h >> 2   //   i >> 432882 H0 >> 0
칼럼 출력 >> [1357008099, Timestamp('2013-01-01 02:41:39'), 182]

2013년 1월 1일 - 2시 41분 45초
d1 >> 1 d >> 1 H1 >> 2 h >> 2   //   i >> 432883 H0 >> 0
칼럼 출력 >> [1357008105, Timestamp('2013-01-01 02:41:45'), 184]

2013년 1월 1일 - 2시 41분 51초
d1 >> 1 d >> 1 H1 >> 2 h >> 2   //   i >> 432884 H0 >> 0
칼럼 출력 >> [1357008111, Timestamp('2013-01-01 02:41:51'), 182]

2013년 1월 1일 - 2시 41분 57초
d1 >> 1 d >> 1 H1 >> 2 h >> 2   //   i >> 432885 H0 >> 0
칼럼 출력 >> [1357008117, Timestamp('2013-01-01 02:41:57'), 182]

2013년 1월 1일 - 2시 

csv 저장 완료!





여기를 거칩니다잇

2013년 1월 1일 - 3시 0분 5초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433054 H0 >> 0
칼럼 출력 >> [1357009205, Timestamp('2013-01-01 03:00:05'), 181]

2013년 1월 1일 - 3시 0분 11초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433055 H0 >> 0
칼럼 출력 >> [1357009211, Timestamp('2013-01-01 03:00:11'), 184]

2013년 1월 1일 - 3시 0분 17초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433056 H0 >> 0
칼럼 출력 >> [1357009217, Timestamp('2013-01-01 03:00:17'), 182]

2013년 1월 1일 - 3시 0분 24초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433057 H0 >> 0
칼럼 출력 >> [1357009224, Timestamp('2013-01-01 03:00:24'), 184]

2013년 1월 1일 - 3시 0분 30초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433058 H0 >> 0
칼럼 출력 >> [1357009230, Timestamp('2013-01-01 03:00:30'), 180]

2013년 1월 1일 - 3시 0분 36초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433059 H0 >> 0
칼럼 출력 >> [1357009236, Timestamp('2013-01-01 03:00:36'), 180]

2013년 1월 1일 - 3시 0분 42초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433060 H0 >> 0
칼럼 출력 >> [1357009242, Timestamp('20

d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433242 H0 >> 0
칼럼 출력 >> [1357010393, Timestamp('2013-01-01 03:19:53'), 240]

2013년 1월 1일 - 3시 19분 59초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433243 H0 >> 0
칼럼 출력 >> [1357010399, Timestamp('2013-01-01 03:19:59'), 238]

2013년 1월 1일 - 3시 20분 5초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433244 H0 >> 0
칼럼 출력 >> [1357010405, Timestamp('2013-01-01 03:20:05'), 239]

2013년 1월 1일 - 3시 20분 11초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433245 H0 >> 0
칼럼 출력 >> [1357010411, Timestamp('2013-01-01 03:20:11'), 234]

2013년 1월 1일 - 3시 20분 18초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433246 H0 >> 0
칼럼 출력 >> [1357010418, Timestamp('2013-01-01 03:20:18'), 238]

2013년 1월 1일 - 3시 20분 24초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433247 H0 >> 0
칼럼 출력 >> [1357010424, Timestamp('2013-01-01 03:20:24'), 236]

2013년 1월 1일 - 3시 20분 30초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433248 H0 >> 0
칼럼 출력 >> [1357010430, Timestamp('2013-01-01 03:20:30'), 240]

2013년 1월 1일 - 3시 2

d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433424 H0 >> 0
칼럼 출력 >> [1357011561, Timestamp('2013-01-01 03:39:21'), 241]

2013년 1월 1일 - 3시 39분 27초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433425 H0 >> 0
칼럼 출력 >> [1357011567, Timestamp('2013-01-01 03:39:27'), 244]

2013년 1월 1일 - 3시 39분 33초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433426 H0 >> 0
칼럼 출력 >> [1357011573, Timestamp('2013-01-01 03:39:33'), 238]

2013년 1월 1일 - 3시 39분 39초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433427 H0 >> 0
칼럼 출력 >> [1357011579, Timestamp('2013-01-01 03:39:39'), 241]

2013년 1월 1일 - 3시 39분 45초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433428 H0 >> 0
칼럼 출력 >> [1357011585, Timestamp('2013-01-01 03:39:45'), 240]

2013년 1월 1일 - 3시 39분 52초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433429 H0 >> 0
칼럼 출력 >> [1357011592, Timestamp('2013-01-01 03:39:52'), 242]

2013년 1월 1일 - 3시 39분 58초
d1 >> 1 d >> 1 H1 >> 3 h >> 3   //   i >> 433430 H0 >> 0
칼럼 출력 >> [1357011598, Timestamp('2013-01-01 03:39:58'), 243]

2013년 1월 1일 - 3시 

KeyboardInterrupt: 

### 이건 카피, 실험용

In [23]:
import time
import csv

# 1.
#i = 431368, 517000, 684157
i = 431368
print('Running!', '\n'*9)

# 2.
while(i < 20284836):
    list1 = ch1_date.loc[i].values.tolist()
            
    # Nested List 사용해서 시간 정보만 따로 추출
    date = list1[1]
    y1 = date.year
    M1 = date.month
    d1 = date.day
    H1 = date.hour # 이 H가 있어야 밑에 있는 하루 단위 반복이 돌 변수가 됨.
    n = 0
    Ho = 0
    # H1는 데이터에서 읽어오는 값이지만 H0는 절대적
    
    # 3. 
    # 하루 단위 반복
    while(H1 < 24):
        
        
        if(H1!=Ho):
            NaC = H1
            while(True):
                print('Ho >>', Ho)
                print('하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~')
                NaC = NaC-1
                if(NaC==1):
                    break
                Ho = Ho+1
            if(H1==Ho):
                break
            break
        
            
        watt_list=[]
        h = date.hour

        # 3.1.
        # h시와 h+1 시 사이 반복
        while(h < h+1):
            n=n+1
            list2 = ch1_date.loc[i].values.tolist()

            date = list2[1]
            watt = list2[2]

            y = date.year
            M = date.month
            d = date.day
            h = date.hour
            m = date.minute
            s = date.second

            print()

            # jump 를 하는 경우가 있기 때문에 이 경우를 구분 짓는 변수를 j로 선택
            j=h-H1

            # 3.1.1.
            # '시'단위가 바뀌기 전에 값들만 저장 (ex. 1시일 경우 2시가 되기전 데이터들만 저장)
            if(j==0):
                watt_list.append(watt) # 1시간 동안 6 or 7초 단위로 읽어오는 watt 값들 전부 추가

                # 확인용 각 변수 출력
                total_date = '{0}년 {1}월 {2}일 - {3}시 {4}분 {5}초'.format(y, M, d, h, m, s)
                print(total_date)
                print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i)
                print('칼럼 출력 >>', list2)

                i = i+1

                if(j!=0):
                    break

            # 3.1.2.    
            # 시가 바뀌는 경우 -------------------------------------------------------------------------------------------------
            elif (j==1):
                print()
                print('시 단위 변경! 루프 종료 및 맥스값 추출!')

                print('========================================< 3.1.2. - 1시간치 끝!! >==================================================')
                print()
                #print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'H0 >>', H0)        이거 나중에 삭제!
                print('1시간 동안 데이터 수 >>', n)
                print()

                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)

                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date2 = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_date5 = '{0}년 {1}월 {2}일'.format(y, M, d)
                hourly_list = []
                hourly_list.append(hourly_date2)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('csv 저장 완료!')

                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)

                break

            # 3.1.3.
            # 1 시간치 정리가 끝나고 다음 날로 넘어가는 경우. 따로 설정함.---------------------------------------------------------
            elif(d1+1==d):
                print('========================================< 3.1.3. - 1시간치 끝!! >==================================================')
                print()
                #print('d1 >>', d1, 'd >>', d, 'H1 >>', H1, 'h >>', h, '  //  ','i >>', i, 'H0 >>', H0)       이거 나중 삭제!
                print('1시간 동안 데이터 수 >>', n)
                print()
                d=d-1
                h=h+24

                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)


                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date3 = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, H1)
                hourly_list = []
                hourly_list.append(hourly_date3)
                hourly_list.append(max_watt)

                # 데이터 저장 
                with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('*csv 저장 완료!')

                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)
                print('========================================< 하루 끝!! >==================================================')
                print('\n'*4)
                break

            # 3.1.4.
            # 1시간 단위 반복 중 에러 발생 경우-------------------------------------------------------------------------------------
            elif (n>600):
                print('wn'*9)
                print('데이터 처리 필요!! 반복 루프 강제 종료')
                print('X'*500)
                print('wn'*9)
                break


            # 3.1.5.
            # 시 단위가 순차적으로 넘어가는 것이 아닌 건너뛰고 점프해버린 경우 ---------------------------------------------------
            else:
                jc=j

                y5 = hourly_date5[:4]
                M5 = hourly_date5[6]
                d5 = hourly_date5[9:10]

                # 일단 해당 시각 존재하는 만큼은 정리해서 맥스값을 추출하고~
                print()
                print('점프! 시 단위 변경! 루프 종료 및 맥스값 추출!')

                print('========================================< 3.1.5. - 1시간치 끝!! >==================================================')
                print()
                print('1시간 동안 데이터 수 >>', n)
                print()

                # 이 지점이 1시간 간격내에서 구해진 watt 값들 중 max를 뽑는 지점.
                max_watt = max(watt_list)
                print(H1, '시까지의 최대값 >>', max_watt)
                time.sleep(1)

                # 1시간 동안이니 해당 시각의 정보를 시 단위까지로 해서 새로 저장
                hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y5, M5, d5, H1)
                hourly_list = []
                hourly_list.append(hourly_date)
                hourly_list.append(max_watt)
                print(hourly_list)

                # 데이터 저장 
                with open("./"+str(y5)+'_'+str(M5)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                    writer = csv.writer(file)
                    writer.writerow(hourly_list)       
                print('*csv 저장 완료!') 

                # 3.1.5.1.
                # 같은 일자 안 중간에서 시간 단위로 데이터가 없는 경우
                if(d1==d):

                    # 건너뛴 횟수만큼 빈 시간대를 Null로 저장
                    while(True):
                        h=h+1
                        # 점프한 시각 이전까지 Null로 입력 
                        hourly_date = '{0}년 {1}월 {2}일 - {3}시'.format(y, M, d, h-j)
                        hourly_list = []
                        hourly_list.append(hourly_date)
                        hourly_list.append('Null')

                        # 데이터 저장 
                        with open("./"+str(y)+'_'+str(M)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                            writer = csv.writer(file)
                            writer.writerow(hourly_list)       
                        print('*csv 저장 완료!')
                        print()

                        jc=jc-1

                        if jc==1:
                            break

                # 3.1.5.2. 
                # 시간 단위로 빈 데이터가 지속되다가 날짜가 다음 날로 넘어가버리는 경우
                else:
                    jc2 = H1

                    # *3.1.2.에서 저장해둔 날짜 정보를 쪼개서 연,월,일로 분해
                    y5 = hourly_date5[:4]
                    M5 = hourly_date5[6]
                    d5 = hourly_date5[9:11]
                    print(y5, M5, d5)

                    while(jc2<23):
                        jc2 = jc2 + 1
                        combine = ' - {0}시'.format(jc2)
                        # 여기서 올바른 날짜가 담긴 리스트가 필요함. 이걸 전에 정보에서 불러오면 끝인데
                        hourly_date5_2 = hourly_date5 + combine
                        hourly_list5_2 = []
                        hourly_list5_2.append(hourly_date5_2)
                        hourly_list5_2.append('Null')

                        # 데이터 저장 
                        with open("./"+str(y5)+'_'+str(M5)+'_'+"House1_Ch1_Electric_Data.csv", 'a', newline='') as file:
                            writer = csv.writer(file)
                            writer.writerow(hourly_list5_2)       
                        print('*csv 저장 완료!')

                H1 = H1+1 # 저장했으니 다음 시각으로 넘어가기 위한 +1
                print('\n'*4)

                break



        print('종료 지점 확인용')
        break

        
    
    # 하루단위 while 여기서 브레이크를 걸고 다음날로 넘어가도록 해야함.
    
# 전체 While문 종료 지점

Running! 










2013년 1월 1일 - 0시 0분 1초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431368
칼럼 출력 >> [1356998401, Timestamp('2013-01-01 00:00:01'), 499]

2013년 1월 1일 - 0시 0분 7초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431369
칼럼 출력 >> [1356998407, Timestamp('2013-01-01 00:00:07'), 500]

2013년 1월 1일 - 0시 0분 13초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431370
칼럼 출력 >> [1356998413, Timestamp('2013-01-01 00:00:13'), 515]

2013년 1월 1일 - 0시 0분 19초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431371
칼럼 출력 >> [1356998419, Timestamp('2013-01-01 00:00:19'), 522]

2013년 1월 1일 - 0시 0분 26초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431372
칼럼 출력 >> [1356998426, Timestamp('2013-01-01 00:00:26'), 508]

2013년 1월 1일 - 0시 0분 32초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431373
칼럼 출력 >> [1356998432, Timestamp('2013-01-01 00:00:32'), 502]

2013년 1월 1일 - 0시 0분 38초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431374
칼럼 출력 >> [1356998438, Timestamp('2013-01-01 00:00:38'), 507]

2013년 1월 1일 - 0시 0분 44초
d1 >> 1 d >> 

d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431591
칼럼 출력 >> [1356999888, Timestamp('2013-01-01 00:24:48'), 482]

2013년 1월 1일 - 0시 24분 54초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431592
칼럼 출력 >> [1356999894, Timestamp('2013-01-01 00:24:54'), 487]

2013년 1월 1일 - 0시 25분 0초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431593
칼럼 출력 >> [1356999900, Timestamp('2013-01-01 00:25:00'), 477]

2013년 1월 1일 - 0시 25분 6초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431594
칼럼 출력 >> [1356999906, Timestamp('2013-01-01 00:25:06'), 480]

2013년 1월 1일 - 0시 25분 12초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431595
칼럼 출력 >> [1356999912, Timestamp('2013-01-01 00:25:12'), 478]

2013년 1월 1일 - 0시 25분 19초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431596
칼럼 출력 >> [1356999919, Timestamp('2013-01-01 00:25:19'), 486]

2013년 1월 1일 - 0시 25분 25초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431597
칼럼 출력 >> [1356999925, Timestamp('2013-01-01 00:25:25'), 483]

2013년 1월 1일 - 0시 25분 31초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431598
칼

2013년 1월 1일 - 0시 46분 37초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431798
칼럼 출력 >> [1357001197, Timestamp('2013-01-01 00:46:37'), 300]

2013년 1월 1일 - 0시 46분 43초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431799
칼럼 출력 >> [1357001203, Timestamp('2013-01-01 00:46:43'), 301]

2013년 1월 1일 - 0시 46분 50초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431800
칼럼 출력 >> [1357001210, Timestamp('2013-01-01 00:46:50'), 297]

2013년 1월 1일 - 0시 46분 56초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431801
칼럼 출력 >> [1357001216, Timestamp('2013-01-01 00:46:56'), 298]

2013년 1월 1일 - 0시 47분 2초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431802
칼럼 출력 >> [1357001222, Timestamp('2013-01-01 00:47:02'), 301]

2013년 1월 1일 - 0시 47분 8초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431803
칼럼 출력 >> [1357001228, Timestamp('2013-01-01 00:47:08'), 296]

2013년 1월 1일 - 0시 47분 14초
d1 >> 1 d >> 1 H1 >> 0 h >> 0   //   i >> 431804
칼럼 출력 >> [1357001234, Timestamp('2013-01-01 00:47:14'), 297]

2013년 1월 1일 - 0시 47분 20초
d1 >> 1 d >> 1 H1 >> 0 h 

csv 저장 완료!





종료 지점 확인용
Ho >> 0
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 2
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 3
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 4
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 5
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 6
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 7
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 8
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 9
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 10
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 11
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 12
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 13
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 14
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 15
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 16
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 17
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 18
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 19
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 20
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 21
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 22
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 23
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 24
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 25
하루 시작부터 비어있슴다~ 날짜 만들어서 채우

Ho >> 1215
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1216
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1217
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1218
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1219
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1220
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1221
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1222
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1223
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1224
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1225
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1226
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1227
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1228
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1229
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1230
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1231
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1232
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1233
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1234
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1235
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1236
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1237
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1238
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 1239
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~


...

Ho >> 48969
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48970
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48971
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48972
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48973
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48974
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48975
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48976
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48977
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48978
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48979
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48980
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48981
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48982
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48983
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48984
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48985
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48986
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48987
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48988
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48989
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48990
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48991
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48992
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 48993
하루 시

Ho >> 50376
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50377
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50378
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50379
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50380
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50381
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50382
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50383
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50384
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50385
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50386
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50387
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50388
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50389
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50390
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50391
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50392
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50393
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50394
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50395
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50396
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50397
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50398
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50399
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 50400
하루 시

Ho >> 51644
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51645
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51646
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51647
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51648
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51649
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51650
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51651
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51652
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51653
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51654
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51655
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51656
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51657
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51658
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51659
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51660
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51661
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51662
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51663
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51664
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51665
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51666
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51667
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 51668
하루 시

Ho >> 52876
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52877
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52878
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52879
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52880
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52881
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52882
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52883
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52884
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52885
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52886
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52887
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52888
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52889
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52890
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52891
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52892
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52893
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52894
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52895
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52896
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52897
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52898
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52899
하루 시작부터 비어있슴다~ 날짜 만들어서 채우세요~
Ho >> 52900
하루 시

KeyboardInterrupt: 

SyntaxError: invalid syntax (Temp/ipykernel_14196/1482378749.py, line 1)